In [1]:
# Load LSTM network and generate text
import sys
import numpy

from keras.models import Sequential
from keras.layers import Dense
from keras.layers import Dropout
from keras.layers import LSTM
from keras.callbacks import ModelCheckpoint
from keras.utils import np_utils

# load ascii text and covert to lowercase


Using TensorFlow backend.


In [2]:
filename = 'all_lyrics_no-umlaut_edited2.txt'


raw_text = open(filename).read()
raw_text = raw_text.lower()

raw_text = raw_text.replace('\x99', '')
raw_text = raw_text.replace('\x80', '')
raw_text = raw_text.replace('\xe2', '')

raw_text = raw_text.replace('"', '')
raw_text = raw_text.replace('(', '')
raw_text = raw_text.replace(')', '')



# create mapping of unique chars to integers, and a reverse mapping
chars = sorted(list(set(raw_text)))
char_to_int = dict((c, i) for i, c in enumerate(chars))
int_to_char = dict((i, c) for i, c in enumerate(chars))
# summarize the loaded data
n_chars = len(raw_text)
n_vocab = len(chars)
print("Total Characters: ", n_chars)
print("Total Vocab: ", n_vocab)


IOError: [Errno 2] No such file or directory: 'all_lyrics_no-umlaut_edited2.txt'

In [6]:

# prepare the dataset of input to output pairs encoded as integers
seq_length = 100
dataX = []
dataY = []
for i in range(0, n_chars - seq_length, 1):
	seq_in = raw_text[i:i + seq_length]
	seq_out = raw_text[i + seq_length]
	dataX.append([char_to_int[char] for char in seq_in])
	dataY.append(char_to_int[seq_out])
n_patterns = len(dataX)
print("Total Patterns: ", n_patterns)
# reshape X to be [samples, time steps, features]
X = numpy.reshape(dataX, (n_patterns, seq_length, 1))
# normalize
X = X / float(n_vocab)
# one hot encode the output variable
y = np_utils.to_categorical(dataY)
# define the LSTM model
model = Sequential()
model.add(LSTM(128, input_shape=(X.shape[1], X.shape[2])))
model.add(Dense(y.shape[1], activation='softmax'))

model.compile(loss='categorical_crossentropy', optimizer='rmsprop')


('Total Patterns: ', 149247)


In [ ]:
#filename = "aws_128_0.0_char_weights-improvement-143-1.5863.hdf5"
#model.load_weights(filename)

# define the checkpoint
filepath="aws_128_0.0_batch32_char_weights-improvement-{epoch:02d}-{loss:.4f}.hdf5"
checkpoint = ModelCheckpoint(filepath, monitor='loss', verbose=1, save_best_only=True, mode='min')
callbacks_list = [checkpoint]

model.fit(X, y, epochs=20, batch_size=32, callbacks=callbacks_list)



Epoch 1/20
149247/149247 [==============================] - 889s - loss: 1.7697   
Epoch 2/20
149247/149247 [==============================] - 889s - loss: 1.7970   
Epoch 3/20
149247/149247 [==============================] - 882s - loss: 1.8084   
Epoch 4/20
149247/149247 [==============================] - 883s - loss: 1.7935   
Epoch 5/20
149247/149247 [==============================] - 884s - loss: 1.7947   
Epoch 6/20
149247/149247 [==============================] - 882s - loss: 1.7969   
Epoch 7/20
149247/149247 [==============================] - 881s - loss: 1.8000   
Epoch 8/20
  7712/149247 [>.............................] - ETA: 843s - loss: 1.7680 

In [8]:

def sample(preds, temperature=1.0):
    # helper function to sample an index from a probability array
    preds = numpy.asarray(preds).astype('float64')
    preds = numpy.log(preds) / temperature
    exp_preds = numpy.exp(preds)
    preds = exp_preds / numpy.sum(exp_preds)
    probas = numpy.random.multinomial(1, preds, 1)
    return numpy.argmax(probas)



In [12]:

# pick a random seed
start = numpy.random.randint(0, len(dataX)-1)
pattern = dataX[start]
print("Seed:")
print("\"", ''.join([int_to_char[value] for value in pattern]), "\"")


for temprt in [0.1, 0.2, 0.5, 1.0, 1.2, 1.5]:
    print("temp = ", temprt, "\n")
# generate characters
    for i in range(200):
        x = numpy.reshape(pattern, (1, len(pattern), 1))
        x = x / float(n_vocab)
        prediction = model.predict(x, verbose=0)
        #index = numpy.argmax(prediction)
        index = sample(numpy.squeeze(prediction), temprt)
        result = int_to_char[index]
        seq_in = [int_to_char[value] for value in pattern]
        sys.stdout.write(result)
        pattern.append(index)
        pattern = pattern[1:len(pattern)]
print("\nDone.")

Seed:
('"', " my life\n\r\ndon't go to school don't make me laugh\r\ncan't hardly spell, can't do math\r\nin the bar or ", '"')
('temp = ', 0.1, '\n')
�hu ��u�� �hu �oun� io �ou �o��
i �o�� you �ou �oun t �ou �ou� �ou �ou �oun t� �i�
�ou �oun �hu �ou �oun �hu �ou �oun t� �o�

�ou �oun �ou �ou �oun �ou �ou �oun 
('temp = ', 0.2, '\n')ro ��u�� �ou


i want you aro wee to go �ou 

a don't want to lave to toere 
io s gonna be the ton to toe

modan't want to mive tou mo mo

i don't wanna ge a pine tou anb

io sou do toe �oin to mo 
ion t want('temp = ', 0.5, '\n')
 to way aou thte tay 
i -o out ano ir ihr ab theh shl


ia to whe you 

an so mowe an  bot t whu ho soik  aod i ban tt makd

iome anbte ii
toa kart
io toe sa�e so peo toerg toet 

ald i kase you ro('temp = ', 1.0, '\n')
eod ml fnls csnsd t watt momhgk oot n,ka nood
you yonnd 
ihgn wu dae g
rnid hfrivy 

ehda iek tieed mnhtstii,
voeu auigsb nr mrtlee

whi c c d can faar ian
tueiswag ermtb ibvbc 
when o neol tou('temp = ', 1.2, '\n'